In [59]:
# Install packages:
# !pip install pandas
# !pip install folium
# !pip install numpy

In [62]:
class Node:
    def __init__(self, street_name, lat, lon): # string, float, float
        self.street_name = street_name # string
        self.lat = lat # float
        self.lon = lon # float
        self.neighbors = [] # array of (Node, float)
        self.neighbor_names = set() # set of create_key
    
    def add_neighbor(self, end_node, weight):  # Node object, float
        if end_node.create_key() not in self.neighbor_names:
            neighbor = (end_node, weight)
            self.neighbors.append(neighbor)
            self.neighbor_names.add(end_node.create_key())
    
    def create_key(self):
        return str(self.lat) + "," + str(self.lon)
    
    @staticmethod
    def create_key_static(lat, lon):
        return str(lat) + "," + str(lon)
            
    def __str__(self):
        neighbor_str = ""
        
        for n in self.neighbors:
            neighbor_str += f"({n[0].street_name}, {n[0].lat}, {n[0].lon})"
        
        return "STREET NAME: " + self.street_name + ", WITH NEIGHBORS: " + neighbor_str

class Graph:
    def __init__(self):
        self.graph = {} # map from create_key(node): Node
        self.size = 0 # integer
    
    # if vertex exists, returns True, otherwise False.
    def add_vertex(self, street_name, lat, lon): # string, float, float
        new_node = Node(street_name, lat, lon)
        key = new_node.create_key()
        
        if key not in self.graph:
            self.graph[key] = new_node
            self.size += 1
            return True
        else:
            # vertex already exists.
            return False
    
    def add_edge_with_keys(self, start_key, end_key, weight=0): # for when you re-create the graph
        if start_key in self.graph and end_key in self.graph:
            self.graph[start_key].add_neighbor(self.graph[end_key], weight)
            self.graph[end_key].add_neighbor(self.graph[start_key], weight)
            return True
        else:
            return False
        
    def add_edge(self, start_lat, start_lon, end_lat, end_lon, weight=0): # create_key_static, create_key_static, float
        start_key = Node.create_key_static(start_lat, start_lon)
        end_key = Node.create_key_static(end_lat, end_lon)
           
        if start_key in self.graph and end_key in self.graph:
            self.graph[start_key].add_neighbor(self.graph[end_key], weight)
            self.graph[end_key].add_neighbor(self.graph[start_key], weight)
            return True
        else:
            return False

    def print(self):
        for key in self.graph:
            print(key, self.graph[key])
            
    def export_nodes(self):
        result = []
        
        for k in self.graph:
            key = k
            lat = self.graph[key].lat
            lon = self.graph[key].lon
            street_name = self.graph[key].street_name
            deez = {
                "key": key,
                "lat": lat,
                "lon": lon,
                "street_name": street_name
            }
            result.append(deez)
        
        return result
    
    def export_edges(self):
        result = []
        
        for k in self.graph:
            neighbors = self.graph[k].neighbors
            
            for n in neighbors:
                key1 = k
                key2 = (n[0].create_key())         
                weight = (n[1])
                deez = {
                    "key1": key1,
                    "key2": key2,
                    "weight": weight
                }
                result.append(deez)
        
        return result
        
# test graph
graph = Graph()

In [66]:
import pandas as pd
import folium
import numpy as np

# read in data and get coordinates:
df = pd.read_csv('real_data.csv')
df["latitude_longitude"] = df["latitude_longitude"].str.strip()
df["latitude_longitude"]= df["latitude_longitude"].str.split(" ", n = -1, expand = False)
df["latitude_longitude"] = df["latitude_longitude"][::-1]
coordinates = df["latitude_longitude"].tolist()

graph = Graph()

for coords in coordinates:
    points = coords[::-1]

    for i in range(0, len(points) - 2, 2):
        lat = points[i]
        lon = points[i + 1]
        street_name_1 = df["street"][test_index]
        next_point_lat = points[i + 2]
        next_point_lon = points[i + 3]
        street_name_2 = df["street"][test_index+1]
        
        graph.add_vertex(street_name_1, lat, lon)
        graph.add_vertex(street_name_2, next_point_lat, next_point_lon)
        next_point_lat = points[i + 2]
        next_point_lon = points[i + 3]
        
        distance = np.sqrt((float(next_point_lat) - float(lat))**2 + (float(next_point_lon) - float(lon))**2)
        graph.add_edge(lat, lon, next_point_lat, next_point_lon, distance)

# only need to run once - create the graph and export to JSON files for nodes and edges:

# edges = graph.export_edges()
# nodes = graph.export_nodes()

# import json

# with open('edges.json', 'w') as fout:
#     json.dump(edges, fout)
    
# with open('nodes.json', 'w') as fout:
#     json.dump(nodes, fout)

In [67]:
# read in the files and re-create the graph.
import json

edges_file = open('edges.json')
vertices_file = open('nodes.json')

edges = json.load(edges_file)
vertices = json.load(vertices_file)

graph = Graph()

for o in vertices:
    graph.add_vertex(o['street_name'], float(o['lat']), float(o['lon']))

for o in edges:
    graph.add_edge_with_keys(o['key1'], o['key2'], float(o['weight']))

graph.print()


40.50056347052719,-74.24968956587347 STREET NAME: CONFERENCE HOUSE PARK GREENWAY, WITH NEIGHBORS: (CONFERENCE HOUSE PARK GREENWAY, 40.50087622728695, -74.24992754986717)(CONFERENCE HOUSE PARK GREENWAY, 40.49944014889296, -74.24934702119957)
40.50087622728695,-74.24992754986717 STREET NAME: CONFERENCE HOUSE PARK GREENWAY, WITH NEIGHBORS: (CONFERENCE HOUSE PARK GREENWAY, 40.50056347052719, -74.24968956587347)(CONFERENCE HOUSE PARK GREENWAY, 40.50228915504668, -74.2513327304861)
40.49944014889296,-74.24934702119957 STREET NAME: CONFERENCE HOUSE PARK GREENWAY, WITH NEIGHBORS: (CONFERENCE HOUSE PARK GREENWAY, 40.50056347052719, -74.24968956587347)(CONFERENCE HOUSE PARK GREENWAY, 40.49871712913556, -74.24915648792326)
40.49871712913556,-74.24915648792326 STREET NAME: CONFERENCE HOUSE PARK GREENWAY, WITH NEIGHBORS: (CONFERENCE HOUSE PARK GREENWAY, 40.49944014889296, -74.24934702119957)(CONFERENCE HOUSE PARK GREENWAY, 40.49804482548253, -74.24893307025533)
40.50228915504668,-74.2513327304861 S

40.69296295801365,-74.01691429854318 STREET NAME: CARDER RD, WITH NEIGHBORS: (CARDER RD, 40.69324523813158, -74.0170610966538)(FERRY LINE ROAD, 40.69279170832488, -74.01542782102348)
40.69279170832488,-74.01542782102348 STREET NAME: FERRY LINE ROAD, WITH NEIGHBORS: (CARDER RD, 40.69296295801365, -74.01691429854318)(FERRY LINE ROAD, 40.69246336589095, -74.01552236448406)(CARDER RD, 40.69253392730966, -74.01410267144277)
40.69246336589095,-74.01552236448406 STREET NAME: FERRY LINE ROAD, WITH NEIGHBORS: (FERRY LINE ROAD, 40.69279170832488, -74.01542782102348)(MOUNT LORETTO GREENWAY, 40.692468781220796, -74.01555167544717)(JACOB RIIS BOARDWALK, 40.69245553928063, -74.01547743390452)
40.70784040417607,-74.01812094189772 STREET NAME: BATTERY PARK CITY GREENWAY, WITH NEIGHBORS: (BATTERY PARK CITY GREENWAY, 40.706873734838055, -74.01850166689033)(CLAYTON ROAD, 40.708128498541896, -74.01871668869431)
40.70845740998242,-74.01739796592196 STREET NAME: SOUTH END AV, WITH NEIGHBORS: (SOUTH END AV, 

40.62933305775474,-73.96800084451304 STREET NAME: AV H, WITH NEIGHBORS: (AV H, 40.62923162569476, -73.96892915899296)(AV H, 40.629434681590205, -73.96707656943629)
40.629434681590205,-73.96707656943629 STREET NAME: AV H, WITH NEIGHBORS: (AV H, 40.62933305775474, -73.96800084451304)(AV H, 40.629542706964244, -73.96608191393524)
40.629542706964244,-73.96608191393524 STREET NAME: AV H, WITH NEIGHBORS: (AV H, 40.629434681590205, -73.96707656943629)(AV H, 40.629654675031226, -73.96508072867448)
40.629654675031226,-73.96508072867448 STREET NAME: AV H, WITH NEIGHBORS: (AV H, 40.629542706964244, -73.96608191393524)(AV H, 40.629738964964965, -73.96414862934522)
40.629738964964965,-73.96414862934522 STREET NAME: AV H, WITH NEIGHBORS: (AV H, 40.629654675031226, -73.96508072867448)(AV H, 40.62984106120779, -73.9632214939498)(ARGYLE RD, 40.63207992987413, -73.96458921991592)
40.62984106120779,-73.9632214939498 STREET NAME: AV H, WITH NEIGHBORS: (AV H, 40.629738964964965, -73.96414862934522)(AV H, 4

40.72842266776214,-73.99967747145703 STREET NAME: BLEECKER ST, WITH NEIGHBORS: (BLEECKER ST, 40.728794605388124, -74.00043499643259)(BLEECKER ST, 40.72806787294338, -73.99895488609395)(THOMPSON ST, 40.72733725648131, -74.00058982700168)
40.72806787294338,-73.99895488609395 STREET NAME: BLEECKER ST, WITH NEIGHBORS: (BLEECKER ST, 40.72842266776214, -73.99967747145703)(BLEECKER ST, 40.72768069839557, -73.99816919395845)(LA GUARDIA PL, 40.72699687547233, -73.9998630819113)(LA GUARDIA PL, 40.7293104422607, -73.99788585718942)
40.72768069839557,-73.99816919395845 STREET NAME: BLEECKER ST, WITH NEIGHBORS: (BLEECKER ST, 40.72806787294338, -73.99895488609395)(W 3 ST, 40.72730356770609, -73.99740391638956)
40.72730356770609,-73.99740391638956 STREET NAME: W 3 ST, WITH NEIGHBORS: (BLEECKER ST, 40.72768069839557, -73.99816919395845)(BLEECKER ST, 40.726931323170106, -73.99665910385221)
40.72968530881749,-73.99860504073311 STREET NAME: W 3 ST, WITH NEIGHBORS: (LA GUARDIA PL, 40.7293104422607, -73.99

40.767494271022834,-73.9593196993551 STREET NAME: 2 AV, WITH NEIGHBORS: (2 AV, 40.76686810036089, -73.95977640579298)(2 AV, 40.76811990994955, -73.95886194709837)(E 70 ST, 40.76815253592776, -73.96089930136289)(E 70 ST, 40.7669488121961, -73.95803101587288)
40.76811990994955,-73.95886194709837 STREET NAME: 2 AV, WITH NEIGHBORS: (2 AV, 40.767494271022834, -73.9593196993551)(2 AV, 40.768797733358156, -73.95836533246687)(E 71 ST, 40.767118914267385, -73.95649564172334)(E 71 ST, 40.768783898523964, -73.96042890740108)
40.765868753886465,-73.95741202512652 STREET NAME: 1 AV, WITH NEIGHBORS: (1 AV, 40.76524232498815, -73.95786874207427)(1 AV, 40.766493435127, -73.95695607057442)
40.768797733358156,-73.95836533246687 STREET NAME: 2 AV, WITH NEIGHBORS: (2 AV, 40.76811990994955, -73.95886194709837)(2 AV, 40.76948404740645, -73.95786679301791)
40.767118914267385,-73.95649564172334 STREET NAME: E 71 ST, WITH NEIGHBORS: (2 AV, 40.76811990994955, -73.95886194709837)(1 AV, 40.766493435127, -73.95695

...

40.68695437786216,-73.89093892122692 STREET NAME: HIGHLAND PARK GREENWAY, WITH NEIGHBORS: (HIGHLAND PARK GREENWAY, 40.6869384017099, -73.89092358391851)(HIGHLAND PARK GREENWAY, 40.68697010228799, -73.89095470139121)
40.68697010228799,-73.89095470139121 STREET NAME: HIGHLAND PARK GREENWAY, WITH NEIGHBORS: (HIGHLAND PARK GREENWAY, 40.68695437786216, -73.89093892122692)(HIGHLAND PARK GREENWAY, 40.686985566877034, -73.89097091850999)
40.686985566877034,-73.89097091850999 STREET NAME: HIGHLAND PARK GREENWAY, WITH NEIGHBORS: (HIGHLAND PARK GREENWAY, 40.68697010228799, -73.89095470139121)(HIGHLAND PARK GREENWAY, 40.687000765316455, -73.89098756312967)
40.687000765316455,-73.89098756312967 STREET NAME: HIGHLAND PARK GREENWAY, WITH NEIGHBORS: (HIGHLAND PARK GREENWAY, 40.686985566877034, -73.89097091850999)(HIGHLAND PARK GREENWAY, 40.687015689497045, -73.89100463053171)
40.687015689497045,-73.89100463053171 STREET NAME: HIGHLAND PARK GREENWAY, WITH NEIGHBORS: (HIGHLAND PARK GREENWAY, 40.68703033

40.8677635286874,-73.79290471820131 STREET NAME: ORCHARD BEACH BOARDWALK, WITH NEIGHBORS: (ORCHARD BEACH BOARDWALK, 40.867884906819086, -73.7927833328142)(ORCHARD BEACH BOARDWALK, 40.86769496476319, -73.79297418705838)
40.869276715505386,-73.79105423191004 STREET NAME: ORCHARD BEACH BOARDWALK, WITH NEIGHBORS: (ORCHARD BEACH BOARDWALK, 40.86931913214799, -73.79098954027329)(ORCHARD BEACH BOARDWALK, 40.869233970364306, -73.7911185460882)
40.869233970364306,-73.7911185460882 STREET NAME: ORCHARD BEACH BOARDWALK, WITH NEIGHBORS: (ORCHARD BEACH BOARDWALK, 40.869276715505386, -73.79105423191004)(ORCHARD BEACH BOARDWALK, 40.86919089942678, -73.79118248279912)
40.86919089942678,-73.79118248279912 STREET NAME: ORCHARD BEACH BOARDWALK, WITH NEIGHBORS: (ORCHARD BEACH BOARDWALK, 40.869233970364306, -73.7911185460882)(ORCHARD BEACH BOARDWALK, 40.86914750358758, -73.791246038481)
40.86914750358758,-73.791246038481 STREET NAME: ORCHARD BEACH BOARDWALK, WITH NEIGHBORS: (ORCHARD BEACH BOARDWALK, 40.869

40.83389061401746,-73.8765316147261 STREET NAME: E 174 ST, WITH NEIGHBORS: (E 174 ST, 40.83388219310033, -73.87659435446402)(E 174 ST, 40.83389606893398, -73.87649098241889)
40.83389606893398,-73.87649098241889 STREET NAME: E 174 ST, WITH NEIGHBORS: (E 174 ST, 40.83389061401746, -73.8765316147261)(E 174 ST, 40.83390284421681, -73.87644050125105)
40.83390284421681,-73.87644050125105 STREET NAME: E 174 ST, WITH NEIGHBORS: (E 174 ST, 40.83389606893398, -73.87649098241889)(E 174 ST, 40.83390869932663, -73.87639688640292)
40.83390869932663,-73.87639688640292 STREET NAME: E 174 ST, WITH NEIGHBORS: (E 174 ST, 40.83390284421681, -73.87644050125105)(E 174 ST, 40.83392467347352, -73.87627787824182)
40.83392467347352,-73.87627787824182 STREET NAME: E 174 ST, WITH NEIGHBORS: (E 174 ST, 40.83390869932663, -73.87639688640292)(E 174 ST, 40.83392898748373, -73.87624574046623)
40.83392898748373,-73.87624574046623 STREET NAME: E 174 ST, WITH NEIGHBORS: (E 174 ST, 40.83392467347352, -73.87627787824182)(E

40.56368599476958,-74.15796725968244 STREET NAME: BROOKFIELD PARK GWY, WITH NEIGHBORS: (BROOKFIELD PARK GWY, 40.563738903532794, -74.15795473482352)(BROOKFIELD PARK GWY, 40.563634807985856, -74.15798882410175)
40.563634807985856,-74.15798882410175 STREET NAME: BROOKFIELD PARK GWY, WITH NEIGHBORS: (BROOKFIELD PARK GWY, 40.56368599476958, -74.15796725968244)(BROOKFIELD PARK GWY, 40.56358623701442, -74.15801905350072)
40.56358623701442,-74.15801905350072 STREET NAME: BROOKFIELD PARK GWY, WITH NEIGHBORS: (BROOKFIELD PARK GWY, 40.563634807985856, -74.15798882410175)(BROOKFIELD PARK GWY, 40.56354113177525, -74.15805741733313)
40.56354113177525,-74.15805741733313 STREET NAME: BROOKFIELD PARK GWY, WITH NEIGHBORS: (BROOKFIELD PARK GWY, 40.56358623701442, -74.15801905350072)(BROOKFIELD PARK GWY, 40.563500278440266, -74.15810324675412)
40.563500278440266,-74.15810324675412 STREET NAME: BROOKFIELD PARK GWY, WITH NEIGHBORS: (BROOKFIELD PARK GWY, 40.56354113177525, -74.15805741733313)(BROOKFIELD PAR

40.77565159093003,-73.91953796308734 STREET NAME: 24 ST, WITH NEIGHBORS: (24 ST, 40.775416392013256, -73.91982713711218)(24 ST, 40.77579859774721, -73.91935721050652)
40.775134055601974,-73.92017488252215 STREET NAME: 24 ST, WITH NEIGHBORS: (24 ST, 40.775416392013256, -73.91982713711218)(24 ST, 40.77402979336246, -73.92153497173497)
40.77579859774721,-73.91935721050652 STREET NAME: 24 ST, WITH NEIGHBORS: (24 ST, 40.77565159093003, -73.91953796308734)(24 ST, 40.776773240580724, -73.91815883293675)
40.77402979336246,-73.92153497173497 STREET NAME: 24 ST, WITH NEIGHBORS: (HOYT AV N, 40.77393147777885, -73.92165606371556)(24 ST, 40.775134055601974, -73.92017488252215)
40.776773240580724,-73.91815883293675 STREET NAME: 24 ST, WITH NEIGHBORS: (24 ST, 40.77721316496481, -73.91761790631102)(24 ST, 40.77579859774721, -73.91935721050652)
40.77353577436522,-73.92084601880677 STREET NAME: CRESCENT ST, WITH NEIGHBORS: (HOYT AV N, 40.77344096773683, -73.92096168163118)(CRESCENT ST, 40.77465195004685

In [68]:
from queue import PriorityQueue

def shortest_path(g, start):
    # other node: shortest distance from source node (map)
    distances = {}
    
    # map from current node to previous node
    previous = {}
    
    # priority queue of (vertex, float)
    pq = PriorityQueue()
    
    # set of strings
    visited = set()
    
    for vertex in g.graph.keys():
        distances[vertex] = float('inf')
        previous[vertex] = None
        
        if vertex != start:
            pq.put((vertex,))
    
    distances[start] = 0
    
    while not pq.empty():
        current_node = pq.get()
        
        for n in g.graph[current_node].neighbors:
            neighbor = n[0]
            distance = n[1]
            
            tempDistance = distances[neighbor.create_key()] + distance
            
            if tempDistance < distances[vertex]:
                distances[vertex] = tempDistance
                previous[vertex] = neighbor
    
    for k in distances.keys():
        if distances[k] != float('inf'):
            print(distances[k])
    
    return distances, previous